<a href="https://colab.research.google.com/github/KauaHenSilva/python_optical_flow_sensor/blob/main/optical_flow_sparce.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Pacotes Externos

In [1]:
import os

In [2]:
if os.path.exists('python_download_file_drive'):
  !cd python_download_file_drive && git pull
else:
  !git clone https://github.com/KauaHenSilva/python_download_file_drive

Already up to date.


In [3]:
%pip install  --upgrade --quiet -r python_download_file_drive/requirements.txt

# baixando arquivos

In [4]:
import zipfile

In [5]:
!python "python_download_file_drive/main.py" "https://drive.google.com/file/d/1xQtcYzenMZg7OWd90aBTKf_wBZf5E6Xr/view?usp=drive_link" arq.zip --fuzzy
if not os.path.exists('arq') and os.path.exists('arq.zip'):
    with zipfile.ZipFile('arq.zip', 'r') as zip_ref:
        zip_ref.extractall('arq')

O arquivo arq.zip já existe


#  Optical Flow Sparce

In [6]:
import cv2
import numpy as np

In [7]:
cap = cv2.VideoCapture("/content/arq/Rastreamento_OpenCV/videos/walking.avi")
ret, frame_init = cap.read()
if not ret:
  raise Exception("Não foi possível ler o vídeo de inicialização.")

In [8]:
fourcc = cv2.VideoWriter_fourcc(*'XVID')
fps = 24
video_saida = cv2.VideoWriter("resultado.avi", fourcc, fps, (frame_init.shape[1], frame_init.shape[0]))

In [9]:
parameters_shitomasi = dict(
    maxCorners = 100,
    qualityLevel = 0.3,
    minDistance = 7
)
parameters_lucas_kanade = dict(
    winSize = (15, 15),
    criteria = (cv2.TERM_CRITERIA_EPS | cv2.TERM_CRITERIA_COUNT, 10, 0.03),
)
colors = np.random.randint(0, 255, (100, 3))

In [10]:
frame_gray_init = cv2.cvtColor(frame_init, cv2.COLOR_BGR2GRAY)
edges = cv2.goodFeaturesToTrack(frame_gray_init, mask = None, **parameters_shitomasi)
mask = np.zeros_like(frame_init)

In [11]:
while True:
    ret, frame = cap.read()
    if not ret:
        break
    frame_gray = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    new_edges, status, erros = cv2.calcOpticalFlowPyrLK(frame_gray_init, frame_gray, edges, None,**parameters_lucas_kanade)
    new = new_edges[status == 1]
    old = edges[status == 1]
    for i, (new, old) in enumerate(zip(new_edges, edges)):
        a, b = new.ravel()
        c, d = old.ravel()
        mask = cv2.line(mask, (int(a), int(b)), (int(c), int(d)), colors[i].tolist(), 2)
        frame = cv2.circle(frame, (int(a), int(b)), 5, colors[i].tolist(), -1)
    img = cv2.add(frame, mask)

    video_saida.write(img)
    frame_gray_init = frame_gray.copy()
    edges = new_edges.reshape(-1, 1, 2)

cap.release()
video_saida.release()

# Exibição de resultado

In [12]:
%pip install --upgrade --quiet ffmpeg-python
import ffmpeg
import base64
import io
from IPython.display import HTML
import tempfile

In [13]:
def compress_video(input_file, output_file, resolution=(640, 360), bitrate="500k"):
    ffmpeg.input(input_file).output(output_file, vf=f'scale={resolution[0]}:{resolution[1]}', video_bitrate=bitrate).run(overwrite_output=True,  quiet=True)

def show_video(name_file, otimized=False):
    if otimized:
        with tempfile.NamedTemporaryFile(suffix=".mp4", delete=False) as temp_video:
            compressed_file = temp_video.name
            compress_video(name_file, compressed_file)
        name_file = compressed_file

    video = io.open(name_file, 'r+b').read()
    encoded = base64.b64encode(video).decode('ascii')

    return HTML(data=f'''
    <video width="640" height="360" controls>
        <source src="data:video/mp4;base64,{encoded}" type="video/mp4">
    </video>''')

In [15]:
!ffmpeg -y -loglevel panic -i resultado.avi resultado.mp4
show_video("resultado.mp4", otimized=False)